# Исследовательский анализ данных

In [1]:
import pandas as pd
import json
import folium
import requests


import numpy as np
from shapely.geometry import LineString, shape, Point, Polygon
from shapely.ops import nearest_points
from shapely.ops import linemerge
from pyproj import Transformer


Загружаем и распаковываем данные, которые мы получили из API.

In [2]:
# Запрос к серверу для получения данных последней миссии
response = requests.get("http://localhost:5005/get-mission")
mission_data = response.json()

drone_data = mission_data.get('droneData', {})
route_points = mission_data.get('routePoints', [])
saved_polygons = mission_data.get('savedPolygons', {})

print(drone_data)
print(route_points)
print(saved_polygons)

{'altitude': 0, 'lat': 55.139592, 'lng': 37.962471}
[{'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.14029728763484, 'lng': 37.962179596137815}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.14071470613979, 'lng': 37.96168113272975}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.141496525878495, 'lng': 37.962307110034345}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.14143689609895, 'lng': 37.96428937149736}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.14095322903958, 'lng': 37.96479942708004}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.140337041966234, 'lng': 37.96439370104815}, {'altitude': 330, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.14025090753162, 'lng': 37.96562247131337}, {'altitude': 33, 'flightAltitude': '', 'groundAltitude': 0, 'lat': 55.139985877335675, 'lng': 37.966468699890754}, {'altitude': 33, 'flightAltitu

Наносим на карту

In [3]:
# Создаём карту
m = folium.Map(location=[drone_data.get('lat', 0), drone_data.get('lng', 0)], zoom_start=16)

# Добавляем маркер дрона красного цвета
folium.Marker(
    [drone_data.get('lat', 0), drone_data.get('lng', 0)],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Добавляем маршрутные точки
for pt in route_points:
    folium.Marker(
        [pt.get('lat', 0), pt.get('lng', 0)],
        popup=f"Информация: {pt.get('lat', 'нет данных'), pt.get('lng', 'нет данных'), pt.get('altitude', 'нет данных')}",
        icon=folium.Icon(color='blue', icon='cloud')  # Можно выбрать любой цвет и иконку
    ).add_to(m)

# Соединяем маршрутные точки пунктирной линией
if len(route_points) > 1:
    folium.PolyLine(
        locations=[(pt.get('lat', 0), pt.get('lng', 0)) for pt in route_points],
        color='blue',
        weight=3,
        opacity=0.7,
        dash_array="5, 5" # пунктир
    ).add_to(m)


# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)



# Добавляем полигоны
if saved_polygons and saved_polygons.get('features'):
    folium.GeoJson(saved_polygons).add_to(m)

# Отображаем карту
m

In [4]:
# # Создаем объект Polygon из первого элемента saved_polygons
#
# polygon_wgs = shape(saved_polygons["features"][0]["geometry"])
# # Проверяем, что тип объекта - Polygon
# assert polygon_wgs.geom_type == 'Polygon'

Преобразуем маршрутные точки в LineString и генерируем новые с шагом 1м

In [5]:
# Преобразование координат: из WGS84 в UTM
# Для Москвы часто используют UTM zone 37N (EPSG:32637), проверьте корректность для вашей области.
transformer_to_m = Transformer.from_crs("epsg:4326", "epsg:32637", always_xy=True)
transformer_to_wgs = Transformer.from_crs("epsg:32637", "epsg:4326", always_xy=True)

# Преобразуем координаты маршрутных точек в UTM
route_coords_m = []
for pt in route_points:
    x, y = transformer_to_m.transform(pt["lng"], pt["lat"])
    route_coords_m.append((x, y))

# Создаем LineString в метрической системе
route_line = LineString(route_coords_m)

# Генерируем новые точки на маршруте с шагом 1 метр
step = 1.0
points_along_route = []
distance = 0.0

while distance <= route_line.length:
    pt = route_line.interpolate(distance)
    points_along_route.append(pt)
    distance += step


In [6]:
# Преобразуем полигон в UTM (для корректных расчетов)
def transform_polygon_to_utm(polygon_wgs, transformer):
    # Получаем координаты полигона, преобразуем каждую точку
    utm_coords = []
    for ring in polygon_wgs.exterior.coords:
        x, y = transformer.transform(ring[0], ring[1])
        utm_coords.append((x, y))
    return Polygon(utm_coords)

# polygon_utm = transform_polygon_to_utm(polygon_wgs, transformer_to_m)

In [7]:
# Преобразуем каждый полигон из saved_polygons в объект Shapely и затем в UTM
polygons_utm = []
for feature in saved_polygons["features"]:
    poly_wgs = shape(feature["geometry"])
    poly_utm = transform_polygon_to_utm(poly_wgs, transformer_to_m)
    polygons_utm.append(poly_utm)

In [8]:
# Функция для вычисления проекции точки на отрезок (ребро)
def point_to_segment_projection(point, seg_start, seg_end):
    """
    point, seg_start, seg_end - кортежи (x, y)
    Возвращает: (projection, distance)
    projection: координаты проекции (x, y)
    distance: расстояние от точки до проекции
    """
    p = np.array(point)
    a = np.array(seg_start)
    b = np.array(seg_end)
    ab = b - a
    if np.allclose(ab, 0):
        return a, np.linalg.norm(p - a)
    t = np.dot(p - a, ab) / np.dot(ab, ab)
    if t < 0:
        projection = a
    elif t > 1:
        projection = b
    else:
        projection = a + t * ab
    distance = np.linalg.norm(p - projection)
    return projection, distance


In [9]:
# Функция для получения ближайшей проекции (перпендикуляра) от точки к границе полигона
def get_nearest_projection_on_polygon(point, polygon):
    """
    point: shapely Point (в UTM)
    polygon: shapely Polygon (в UTM)
    Возвращает: (projection, distance), где projection - кортеж (x, y)
    """
    coords = list(polygon.exterior.coords)
    min_distance = float('inf')
    best_proj = None
    # Проходим по каждому ребру полигона
    for i in range(len(coords) - 1):  # последний элемент равен первому
        a = coords[i]
        b = coords[i+1]
        proj, dist = point_to_segment_projection((point.x, point.y), a, b)
        if dist < min_distance:
            min_distance = dist
            best_proj = proj
    return best_proj, min_distance

In [10]:
# Функция для перебора всех полигонов и выбора проекции с минимальным расстоянием
def get_nearest_projection(point, polygons):
    overall_best_proj = None
    overall_min_dist = float('inf')
    for poly in polygons:
        proj, dist = get_nearest_projection_on_polygon(point, poly)
        if dist < overall_min_dist:
            overall_min_dist = dist
            overall_best_proj = proj
    return overall_best_proj, overall_min_dist

In [11]:
# Для каждой сгенерированной точки вдоль маршрута находим проекцию на ближайшее ребро полигона
projections = []
for pt in points_along_route:
    best_proj, d = get_nearest_projection(pt, polygons_utm)
    projections.append((pt, Point(best_proj)))

In [12]:
# Преобразуем точки и проекции обратно в WGS84 для отображения
points_along_route_wgs = []
projections_wgs = []
for pt, proj_pt in projections:
    lng_pt, lat_pt = transformer_to_wgs.transform(pt.x, pt.y)
    lng_proj, lat_proj = transformer_to_wgs.transform(proj_pt.x, proj_pt.y)
    points_along_route_wgs.append((lat_pt, lng_pt))
    projections_wgs.append((lat_proj, lng_proj))

In [13]:
# Отрисовка на карте с помощью Folium
m = folium.Map(location=[drone_data["lat"], drone_data["lng"]], zoom_start=16)

# Маркер дрона (красный)
folium.Marker(
    [drone_data["lat"], drone_data["lng"]],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Отобразим сгенерированные точки маршрута (синие кружки)
for pt in points_along_route_wgs:
    folium.CircleMarker(
        location=pt,
        radius=1,
        color='blue',
        fill=True,
        fill_color='blue'
    ).add_to(m)

# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)

# Соединяем последовательные маршрутные точки (пунктирной линией)
folium.PolyLine(
    locations=[(pt["lat"], pt["lng"]) for pt in route_points],
    color="blue",
    weight=3,
    opacity=0.7,
    dash_array="5, 5"
).add_to(m)

# Отображаем полигоны через GeoJson
folium.GeoJson(saved_polygons).add_to(m)

# Отображаем линии-перпендикуляры (зеленые) для каждой точки
for pt, proj_pt in zip(points_along_route_wgs, projections_wgs):
    folium.PolyLine(
        locations=[pt, proj_pt],
        color="green",
        weight=1,
        opacity=0.8,
        dash_array="2, 4"
    ).add_to(m)

m

Отступаем произвольное число в метрах от точки соприкосновения каждого полигона с высотами на самой проекции

In [14]:
offset_distance = 3.0  # отступ в метрах

# Предполагаем, что projections имеет формат: [(pt, proj_pt), ...]
# где pt – исходная точка (shapely.Point) вдоль маршрута (в UTM),
# а proj_pt – проекция этой точки на полигон (также shapely.Point, в UTM)

corrected_projections = []
for pt, proj_pt in projections:
    # Вычисляем вектор от проекции к исходной точке
    v = np.array([pt.x - proj_pt.x, pt.y - proj_pt.y])
    norm_v = np.linalg.norm(v)
    if norm_v == 0:
        # Если вектор нулевой, оставляем проекцию без смещения
        corrected_point = proj_pt
    else:
        unit_v = v / norm_v
        corrected_coords = np.array([proj_pt.x, proj_pt.y]) + offset_distance * unit_v
        corrected_point = Point(corrected_coords)
    corrected_projections.append(corrected_point)

In [15]:
corrected_points_wgs = []
for cp in corrected_projections:
    lng, lat = transformer_to_wgs.transform(cp.x, cp.y)
    corrected_points_wgs.append((lat, lng))

In [16]:
# Создаем карту
m = folium.Map(location=[drone_data["lat"], drone_data["lng"]], zoom_start=16)

# Отрисовываем полигоны
if saved_polygons and saved_polygons.get('features'):
    folium.GeoJson(saved_polygons, style_function=lambda x: {
        'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3
    }).add_to(m)

# Добавляем маркер дрона
folium.Marker(
    [drone_data["lat"], drone_data["lng"]],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)

# Отрисовываем исходный маршрут (например, пунктирной линией) по исходным точкам
folium.PolyLine(
    locations=[(pt["lat"], pt["lng"]) for pt in route_points],
    color="blue",
    weight=3,
    opacity=0.7,
    dash_array="5,5"
).add_to(m)

# Отображаем смещённые точки скорректированного маршрута (зелёные кружки)
for pt in corrected_points_wgs:
    folium.CircleMarker(
        location=pt,
        radius=2,
        color='green',
        fill=True,
        fill_color='green'
    ).add_to(m)

# Соединяем смещённые точки линией (скорректированная миссия)
folium.PolyLine(
    locations=corrected_points_wgs,
    color="green",
    weight=3,
    opacity=0.8
).add_to(m)

m

## Проработка алгоритма огибания пересекаемых участков полигонов

In [17]:
# Функция для преобразования (lng, lat) в (lat, lng) для Folium
def to_latlon(coord):
    return (coord[1], coord[0])

# Формируем исходный маршрут (shapely LineString, координаты: (lng, lat))
route_line = LineString([(pt['lng'], pt['lat']) for pt in route_points])
route_coords = list(route_line.coords)

# Функция для корректировки одного сегмента маршрута, если он пересекает полигон
def correct_segment(segment, poly):
    """
    segment: LineString (два узловых точки)
    polygons: список объектов Polygon
    Если сегмент пересекается с каким-либо полигоном, возвращает скорректированный LineString,
    иначе возвращает исходный segment.
    """
    for poly in polygons:
        if segment.intersects(poly):
            # Вычисляем пересечение
            intersection = segment.intersection(poly)
            if intersection.is_empty:
                continue
            # Определяем точки входа и выхода для этого сегмента:
            if intersection.geom_type == 'LineString':
                entry = Point(intersection.coords[0])
                exit = Point(intersection.coords[-1])
            elif intersection.geom_type == 'MultiLineString':
                merged = linemerge(intersection)
                if merged.geom_type == 'LineString':
                    entry = Point(merged.coords[0])
                    exit = Point(merged.coords[-1])
                else:
                    pts = []
                    for ls in merged.geoms:
                        pts.extend(list(ls.coords))
                    entry = Point(min(pts, key=lambda c: segment.project(Point(c))))
                    exit = Point(max(pts, key=lambda c: segment.project(Point(c))))
            elif intersection.geom_type == 'MultiPoint':
                pts = list(intersection)
                entry, exit = pts[0], pts[-1]
            else:
                continue

            # Получаем границу полигона
            boundary = poly.exterior
            entry_dist = boundary.project(entry)
            exit_dist = boundary.project(exit)
            if entry_dist > exit_dist:
                entry_dist, exit_dist = exit_dist, entry_dist

            # Кандидат 1: обход от точки входа до точки выхода по границе
            candidate1_coords = [boundary.interpolate(d).coords[0] for d in np.linspace(entry_dist, exit_dist, num=20)]
            candidate1_line = LineString(candidate1_coords)
            total_length = boundary.length
            # Кандидат 2: обход в обратную сторону (через остаток границы)
            candidate2_coords = [boundary.interpolate(d % total_length).coords[0]
                                 for d in np.linspace(entry_dist, entry_dist + total_length - (exit_dist - entry_dist), num=20)]
            candidate2_line = LineString(candidate2_coords)
            bypass = candidate1_line if candidate1_line.length < candidate2_line.length else candidate2_line

            # Формируем скорректированный сегмент:
            # От начала сегмента до точки входа, затем обходной сегмент, затем от точки выхода до конца сегмента.
            seg_coords = list(segment.coords)
            # Находим ближайшие индексы для точек входа и выхода в сегменте
            def find_nearest_index(coords, pt):
                dists = [Point(coord).distance(pt) for coord in coords]
                return np.argmin(dists)
            entry_index = find_nearest_index(seg_coords, entry)
            exit_index = find_nearest_index(seg_coords, exit)
            if entry_index > exit_index:
                entry_index, exit_index = exit_index, entry_index
            new_seg_coords = seg_coords[:entry_index+1] + list(bypass.coords) + seg_coords[exit_index:]
            return LineString(new_seg_coords)
    return segment  # если пересечений нет

# Преобразуем список сохранённых полигонов в объекты shapely Polygon
polygons = [Polygon(feature['geometry']['coordinates'][0]) for feature in saved_polygons['features']]

# Разбиваем исходный маршрут на сегменты (каждый отрезок между двумя соседними точками)
segments = []
for i in range(len(route_coords) - 1):
    seg = LineString([route_coords[i], route_coords[i+1]])
    segments.append(seg)

# Обрабатываем каждый сегмент:
corrected_segments = []
for seg in segments:
    corrected_seg = correct_segment(seg, polygons)
    corrected_segments.append(corrected_seg)

# Объединяем скорректированные сегменты в один маршрут
corrected_coords = []
for seg in corrected_segments:
    coords = list(seg.coords)
    if corrected_coords and coords[0] == corrected_coords[-1]:
        corrected_coords.extend(coords[1:])
    else:
        corrected_coords.extend(coords)
corrected_route = LineString(corrected_coords)


In [18]:
# --- Отрисовка на карте с Folium ---
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=15)

# Отображаем полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)

# Отображаем исходный маршрут (синяя пунктирная линия)
folium.PolyLine(
    locations=[to_latlon(coord) for coord in route_line.coords],
    color='blue',
    weight=3,
    opacity=0.7,
    dash_array='5,5'
).add_to(m)

# Отображаем скорректированный маршрут (зелёная линия)
folium.PolyLine(
    locations=[to_latlon(coord) for coord in corrected_route.coords],
    color='green',
    weight=3,
    opacity=0.8
).add_to(m)

# Маркер дрона (красный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)

m

In [19]:
import folium
import numpy as np
from shapely.geometry import LineString, Polygon, Point
from shapely.ops import linemerge

# Функция для преобразования координат (lng, lat) -> (lat, lng) для Folium
def to_latlon(coord):
    return (coord[1], coord[0])

# Функция для разрезания линии (LineString) на две части в заданном расстоянии
def cut(line, distance):
    """
    Разрезает LineString line на две части в точке, находящейся на расстоянии distance от начала.
    Возвращает список из двух LineString.
    Если distance вне диапазона, возвращает оригинальный line в одном элементе списка.
    """
    if distance <= 0.0 or distance >= line.length:
        return [LineString(line.coords)]
    coords = list(line.coords)
    for i, p in enumerate(coords):
        pd = line.project(Point(p))
        if np.isclose(pd, distance):
            return [
                LineString(coords[:i+1]),
                LineString(coords[i:])
            ]
        if pd > distance:
            cp = line.interpolate(distance)
            return [
                LineString(coords[:i] + [(cp.x, cp.y)]),
                LineString([(cp.x, cp.y)] + coords[i:])
            ]

# Функция для объединения нескольких LineString по их координатам
def merge_lines(lines):
    merged_coords = []
    for line in lines:
        coords = list(line.coords)
        if merged_coords and np.allclose(coords[0], merged_coords[-1]):
            merged_coords.extend(coords[1:])
        else:
            merged_coords.extend(coords)
    return LineString(merged_coords)

# Функция для корректировки одного сегмента маршрута, заменяя лишь часть, которая проходит через полигон
def refined_correct_segment(segment, poly):
    """
    Если сегмент пересекается с полигоном, вычисляет расстояния вдоль segment, где начинается и заканчивается пересечение.
    Затем разрезает segment на safe части (до входа и после выхода) и заменяет внутреннюю часть обходным сегментом,
    вычисляемым вдоль границы полигона между проекциями этих точек.
    Если сегмент не пересекается с poly – возвращает segment без изменений.
    """
    if not segment.intersects(poly):
        return segment

    # Вычисляем пересечение сегмента с полигоном
    intersection = segment.intersection(poly)
    if intersection.is_empty:
        return segment

    # Обработка типов пересечения: предпочитаем LineString или объединяем MultiLineString
    if intersection.geom_type == 'LineString':
        entry = Point(intersection.coords[0])
        exit = Point(intersection.coords[-1])
    elif intersection.geom_type == 'MultiLineString':
        merged = linemerge(intersection)
        if merged.geom_type == 'LineString':
            entry = Point(merged.coords[0])
            exit = Point(merged.coords[-1])
        else:
            pts = []
            for ls in merged.geoms:
                pts.extend(list(ls.coords))
            entry = Point(min(pts, key=lambda c: segment.project(Point(c))))
            exit = Point(max(pts, key=lambda c: segment.project(Point(c))))
    elif intersection.geom_type == 'MultiPoint':
        pts = list(intersection)
        entry, exit = pts[0], pts[-1]
    else:
        # Если тип пересечения не предвиден, ничего не меняем
        return segment

    # Определяем расстояния вдоль сегмента для точек входа и выхода
    d_entry = segment.project(entry)
    d_exit = segment.project(exit)
    if d_entry > d_exit:
        d_entry, d_exit = d_exit, d_entry

    # Разрезаем сегмент на три части
    parts = []
    if d_entry > 0:
        parts.append(cut(segment, d_entry)[0])
    # Центральная часть, которую заменим – от d_entry до d_exit
    central_parts = cut(segment, d_entry)
    if len(central_parts) == 2:
        central_part = central_parts[1]
        central_parts = cut(central_part, d_exit - d_entry)
        if len(central_parts) == 2:
            central_inside = central_parts[0]
        else:
            central_inside = central_part
    else:
        central_inside = segment
    if d_exit < segment.length:
        parts.append(cut(segment, d_exit)[1])

    # Теперь вычисляем обходной сегмент вдоль границы полигона между проекциями точек entry и exit.
    # Находим проекции entry и exit на границу полигона.
    boundary = poly.exterior
    proj_entry = Point(boundary.interpolate(boundary.project(entry)).coords[0])
    proj_exit  = Point(boundary.interpolate(boundary.project(exit)).coords[0])
    # Вычисляем расстояния вдоль границы
    b_entry = boundary.project(proj_entry)
    b_exit  = boundary.project(proj_exit)
    if b_entry > b_exit:
        b_entry, b_exit = b_exit, b_entry

    candidate1_coords = [boundary.interpolate(d).coords[0] for d in np.linspace(b_entry, b_exit, num=20)]
    candidate1_line = LineString(candidate1_coords)
    total_length = boundary.length
    candidate2_coords = [boundary.interpolate(d % total_length).coords[0] for d in np.linspace(b_entry, b_entry + total_length - (b_exit - b_entry), num=20)]
    candidate2_line = LineString(candidate2_coords)
    bypass = candidate1_line if candidate1_line.length < candidate2_line.length else candidate2_line

    # Формируем новый сегмент: безопасная часть до d_entry, затем обходной сегмент, затем безопасная часть после d_exit.
    safe_before = cut(segment, d_entry)[0] if d_entry > 0 else None
    safe_after = cut(segment, d_exit)[1] if d_exit < segment.length else None

    new_coords = []
    if safe_before is not None:
        new_coords.extend(list(safe_before.coords))
    new_coords.extend(list(bypass.coords))
    if safe_after is not None:
        # Избегаем дублирования последней координаты обхода
        new_coords.extend(list(safe_after.coords)[1:])
    return LineString(new_coords)

# Итеративная корректировка маршрута для всех сегментов и для всех полигонов
def refine_route_for_polygons(route_line, polygons):
    route_coords = list(route_line.coords)
    # Разбиваем исходный маршрут на сегменты между соседними точками
    segments = [LineString([route_coords[i], route_coords[i+1]]) for i in range(len(route_coords)-1)]
    corrected_segments = []
    for seg in segments:
        corrected_seg = seg
        for poly in polygons:
            corrected_seg = refined_correct_segment(corrected_seg, poly)
        corrected_segments.append(corrected_seg)
    # Объединяем скорректированные сегменты
    new_coords = []
    for seg in corrected_segments:
        seg_coords = list(seg.coords)
        if new_coords and np.allclose(seg_coords[0], new_coords[-1]):
            new_coords.extend(seg_coords[1:])
        else:
            new_coords.extend(seg_coords)
    return LineString(new_coords)

# Преобразуем сохранённые полигоны в объекты Polygon
polygons = [Polygon(feature['geometry']['coordinates'][0]) for feature in saved_polygons['features']]

# Получаем скорректированный маршрут
corrected_route = refine_route_for_polygons(route_line, polygons)

# --- Отрисовка на карте с Folium ---
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=15)

# Отображаем полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)

# Отображаем исходный маршрут (синяя пунктирная линия)
folium.PolyLine(
    locations=[to_latlon(coord) for coord in route_line.coords],
    color='blue',
    weight=3,
    opacity=0.7,
    dash_array='5,5'
).add_to(m)

# Отображаем скорректированный маршрут (зелёная линия)
folium.PolyLine(
    locations=[to_latlon(coord) for coord in corrected_route.coords],
    color='orange',
    weight=3,
    opacity=0.8
).add_to(m)

# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)

# Маркер дрона (красный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

m

Теперь генерируем точки с шагом в 1м

In [20]:
# Создаем трансформеры: из WGS84 в UTM (например, для Москвы используется EPSG:32637)
transformer_to_m = Transformer.from_crs("epsg:4326", "epsg:32637", always_xy=True)
transformer_to_wgs = Transformer.from_crs("epsg:32637", "epsg:4326", always_xy=True)

# Функция для преобразования точки (shapely Point) из UTM обратно в (lat, lng)
def point_to_wgs(pt):
    lng, lat = transformer_to_wgs.transform(pt.x, pt.y)
    return (lat, lng)

# Преобразуем исходный маршрут в UTM
route_coords_m = [transformer_to_m.transform(lng, lat) for (lng, lat) in route_line.coords]
original_route_m = LineString(route_coords_m)

# Преобразуем corrected_route (в WGS84) в UTM
corrected_coords_m = [transformer_to_m.transform(lng, lat) for (lng, lat) in corrected_route.coords]
corrected_route_m = LineString(corrected_coords_m)

# Функция генерации точек вдоль линии с заданным шагом (в метрах)
def generate_points(line, step):
    points = []
    d = 0.0
    while d <= line.length:
        pt = line.interpolate(d)
        points.append(pt)
        d += step
    return points

step = 1.0  # 1 метр
# Генерируем точки вдоль скорректированного маршрута в UTM
corrected_points_m = generate_points(corrected_route_m, step)

# Разделяем точки: если расстояние до оригинального маршрута (original_route_m) меньше порога,
# считаем, что точка совпадает с исходным маршрутом (safe), иначе – принадлежит обходу (boundary).
tolerance = 1.0  # порог в метрах
safe_points_m = []
boundary_points_m = []

for pt in corrected_points_m:
    if pt.distance(original_route_m) < tolerance:
        safe_points_m.append(pt)
    else:
        boundary_points_m.append(pt)

# Преобразуем обе группы точек обратно в WGS84
safe_points_wgs = [point_to_wgs(pt) for pt in safe_points_m]
boundary_points_wgs = [point_to_wgs(pt) for pt in boundary_points_m]


In [21]:
# Визуализация на карте с Folium
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=15)

# Отображаем исходный маршрут (синяя пунктирная линия)
def to_latlon(coord):
    # coord: (lng, lat)
    return (coord[1], coord[0])


# Отображаем полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)


folium.PolyLine(
    locations=[to_latlon(coord) for coord in route_line.coords],
    color='blue', weight=3, opacity=0.7, dash_array='5,5'
).add_to(m)

# Отображаем исходный маршрут (синяя пунктирная линия)
folium.PolyLine(
    locations=[to_latlon(coord) for coord in route_line.coords],
    color='blue',
    weight=3,
    opacity=0.7,
    dash_array='5,5'
).add_to(m)


# Соединяем дрон с первой маршрутной точкой (если маршрут не пуст)
if route_points:
    first_point = route_points[0]
    folium.PolyLine(
        locations=[
            (drone_data.get('lat', 0), drone_data.get('lng', 0)),
            (first_point.get('lat', 0), first_point.get('lng', 0))
        ],
        color="red",
        weight=2,
        opacity=0.7,
        dash_array="5, 5"
    ).add_to(m)

# Маркер дрона (красный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# # Отображаем скорректированный маршрут (зелёная линия)
# folium.PolyLine(
#     locations=[to_latlon(coord) for coord in corrected_route.coords],
#     color='green', weight=3, opacity=0.8
# ).add_to(m)

# Отображаем safe_points (например, оранжевые кружки)
for pt in safe_points_wgs:
    folium.CircleMarker(location=pt, radius=2, color='orange', fill=True, fill_color='orange').add_to(m)

# Отображаем boundary_points (например, фиолетовые кружки)
for pt in boundary_points_wgs:
    folium.CircleMarker(location=pt, radius=2, color='purple', fill=True, fill_color='purple').add_to(m)

# Маркер дрона (красный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон', icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

m


Опускаем проекции

In [22]:
# Функция для вычисления проекции точки на отрезок с помощью векторной математики
def point_to_segment_projection(point, seg_start, seg_end):
    """
    point, seg_start, seg_end: массивы или кортежи (x, y) в UTM
    Возвращает: (projection, distance)
    projection: координаты проекции (x, y)
    distance: расстояние от точки до проекции
    """
    p = np.array(point)
    a = np.array(seg_start)
    b = np.array(seg_end)
    ab = b - a
    if np.allclose(ab, 0):
        return a, np.linalg.norm(p - a)
    t = np.dot(p - a, ab) / np.dot(ab, ab)
    # Ограничиваем t в интервале [0, 1]
    t = max(0, min(1, t))
    projection = a + t * ab
    distance = np.linalg.norm(p - projection)
    return projection, distance

# Смещает точку, лежащую на границе полигона (poly), наружу на offset_distance метров.
def shift_point_outward(point, poly, offset_distance, delta=0.1):
    """
    point: shapely Point в UTM (точка на границе полигона).
    poly: shapely Polygon в UTM.
    offset_distance: смещение (в метрах).
    delta: небольшое смещение вдоль границы для вычисления касательного вектора.

    Возвращает: новую точку (shapely Point в UTM), смещённую наружу.
    """
    boundary = poly.exterior
    # Находим параметр проекции точки на границу
    t = boundary.project(point)
    # Получаем две близкие точки вдоль границы для вычисления касательного вектора
    try:
        p_prev = boundary.interpolate(t - delta)
        p_next = boundary.interpolate(t + delta)
    except Exception:
        p_prev = point
        p_next = point
    tangent = np.array([p_next.x - p_prev.x, p_next.y - p_prev.y])
    norm = np.linalg.norm(tangent)
    if norm == 0:
        return point
    tangent /= norm
    # Вычисляем правую нормаль: (v_y, -v_x)
    normal = np.array([tangent[1], -tangent[0]])
    # Предварительное смещение
    shifted_coords = np.array([point.x, point.y]) + offset_distance * normal
    shifted_point = Point(shifted_coords)
    # Если смещённая точка оказывается внутри полигона, смещаем в противоположную сторону
    if poly.contains(shifted_point):
        shifted_coords = np.array([point.x, point.y]) - offset_distance * normal
        shifted_point = Point(shifted_coords)
    return shifted_point

# Функция для преобразования полигона (shapely Polygon в WGS84) в UTM
def transform_polygon_to_utm(poly_wgs, transformer):
    # Получаем внешнюю оболочку полигона
    coords = list(poly_wgs.exterior.coords)
    # Если контур не замкнут, добавляем первую точку
    if coords[0] != coords[-1]:
        coords.append(coords[0])
    utm_coords = [transformer.transform(lon, lat) for (lon, lat) in coords]
    return Polygon(utm_coords)

# Функция для вычисления проекции точки на ближайшую границу среди всех полигонов
def project_point_to_polygons(point_wgs, polygons_utm, transformer_to_m):
    """
    point_wgs: кортеж (lat, lng) – точка в WGS84
    polygons_utm: список объектов Polygon в UTM
    Возвращает: (best_proj, best_dist) где best_proj – проекция точки (в UTM), best_dist – расстояние.
    """
    # Преобразуем точку в UTM; transformer_to_m требует (lon, lat)
    x, y = transformer_to_m.transform(point_wgs[1], point_wgs[0])
    p_utm = np.array([x, y])
    best_proj = None
    best_dist = float('inf')
    for poly in polygons_utm:
        coords = list(poly.exterior.coords)
        # Проходим по каждому ребру полигона
        for i in range(len(coords)-1):
            a = coords[i]
            b = coords[i+1]
            proj, dist = point_to_segment_projection(p_utm, a, b)
            if dist < best_dist:
                best_dist = dist
                best_proj = proj
    return best_proj, best_dist

In [23]:
# Преобразуем сохранённые полигоны в объекты Polygon в UTM
polygons_utm = []
for feature in saved_polygons["features"]:
    poly_wgs = shape(feature["geometry"])
    poly_utm = transform_polygon_to_utm(poly_wgs, transformer_to_m)
    polygons_utm.append(poly_utm)

In [24]:
# Для каждой safe точки (из safe_points_wgs) вычисляем проекцию на ближайшую границу полигона.
projected_safe_points_wgs = []
for pt in safe_points_wgs:
    proj, dist = project_point_to_polygons(pt, polygons_utm, transformer_to_m)
    # Преобразуем проекцию (в UTM) обратно в WGS84
    lng, lat = transformer_to_wgs.transform(proj[0], proj[1])
    projected_safe_points_wgs.append((lat, lng))

In [25]:
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=15)

# Отображаем сохранённые полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)

# Отображаем safe_points (оранжевые кружки)
for pt in safe_points_wgs:
    folium.CircleMarker(
        location=pt, radius=3, color='orange', fill=True, fill_color='orange'
    ).add_to(m)

# Отображаем boundary_points (например, фиолетовые кружки)
for pt in boundary_points_wgs:
    folium.CircleMarker(location=pt, radius=2, color='purple', fill=True, fill_color='purple').add_to(m)

# Отображаем проекции для safe точек (синие кружки)
# for pt in projected_safe_points_wgs:
#     folium.CircleMarker(
#         location=pt, radius=3, color='blue', fill=True, fill_color='blue'
#     ).add_to(m)

# Соединяем исходные safe точки с их проекциями линией (например, пунктирной)
for orig, proj in zip(safe_points_wgs, projected_safe_points_wgs):
    folium.PolyLine(
        locations=[orig, proj], color='yellow', weight=2, opacity=0.8, dash_array='2,4'
    ).add_to(m)

# Маркер дрона (красный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон', icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

m

Отмеряем 3 метра от точки сопряжения проекций с гранями полигонов - это будет часть нового маршрута. Добавим условие, чтобы точки не генерировались внутри полигона.

In [31]:
# ------------------------------
# 2. Трансформеры: WGS84 <-> UTM
# ------------------------------

# Для Москвы часто используют UTM zone 37N (EPSG:32637)
transformer_to_m = Transformer.from_crs("epsg:4326", "epsg:32637", always_xy=True)
transformer_to_wgs = Transformer.from_crs("epsg:32637", "epsg:4326", always_xy=True)

def utm_point_to_wgs(pt):
    lng, lat = transformer_to_wgs.transform(pt.x, pt.y)
    return (lat, lng)

# ------------------------------
# 3. Преобразование полигона в UTM
# ------------------------------

def transform_polygon_to_utm(poly_wgs, transformer):
    coords = list(poly_wgs.exterior.coords)
    if coords[0] != coords[-1]:
        coords.append(coords[0])
    utm_coords = [transformer.transform(lon, lat) for (lon, lat) in coords]
    return Polygon(utm_coords)

from shapely.geometry import shape
poly_wgs = shape(saved_polygons["features"][0]["geometry"])
poly_utm = transform_polygon_to_utm(poly_wgs, transformer_to_m)

# ------------------------------
# 4. Фильтрация проекций по safe точкам
# ------------------------------
# Для каждой пары (pt, proj_pt) в projections преобразуем pt в WGS84 и проверяем,
# близка ли она (с учетом tolerance) к одной из safe_points_wgs.
tolerance = 1e-5
safe_projections = []
for pt, proj_pt in projections:
    # Преобразуем исходную точку pt из UTM в WGS84
    pt_wgs = utm_point_to_wgs(pt)
    # Если расстояние до хотя бы одной safe точки меньше tolerance, оставляем эту пару
    if any(np.linalg.norm(np.array(pt_wgs) - np.array(safe_pt)) < tolerance for safe_pt in safe_points_wgs):
        safe_projections.append((pt, proj_pt))

# ------------------------------
# 5. Вычисление corrected_projections для safe проекций
# ------------------------------
offset_distance = 3.0  # смещение в метрах

def shift_point_outward_iterative(pt, proj_pt, poly, initial_offset=3.0, max_iterations=10, increment=1.0):
    """
    Смещает проекцию (proj_pt) вдоль вектора от proj_pt к pt.
    Если полученная точка оказывается внутри полигона, смещение увеличивается.
    Возвращает corrected точку (в UTM) или None, если не удалось получить точку вне полигона.
    """
    v = np.array([pt.x - proj_pt.x, pt.y - proj_pt.y])
    norm_v = np.linalg.norm(v)
    if norm_v == 0:
        return proj_pt
    unit_v = v / norm_v
    offset = initial_offset
    candidate = None
    for i in range(max_iterations):
        candidate = Point(np.array([proj_pt.x, proj_pt.y]) + offset * unit_v)
        if not poly.contains(candidate):
            return candidate
        offset += increment
    return None

corrected_projections = []
for pt, proj_pt in safe_projections:
    v = np.array([pt.x - proj_pt.x, pt.y - proj_pt.y])
    norm_v = np.linalg.norm(v)
    if norm_v == 0:
        candidate = proj_pt
    else:
        unit_v = v / norm_v
        candidate = Point(np.array([proj_pt.x, proj_pt.y]) + offset_distance * unit_v)
        if poly_utm.contains(candidate):
            candidate = shift_point_outward_iterative(pt, proj_pt, poly_utm, initial_offset=offset_distance)
    if candidate is None or poly_utm.contains(candidate):
        print("Предупреждение: кандидат всё ещё внутри полигона — пропускаем эту пару!")
        continue
    corrected_projections.append(candidate)

# Преобразуем corrected_projections в WGS84
corrected_points_wgs = []
for cp in corrected_projections:
    lng, lat = transformer_to_wgs.transform(cp.x, cp.y)
    corrected_points_wgs.append((lat, lng))


Предупреждение: кандидат всё ещё внутри полигона — пропускаем эту пару!
Предупреждение: кандидат всё ещё внутри полигона — пропускаем эту пару!
Предупреждение: кандидат всё ещё внутри полигона — пропускаем эту пару!
Предупреждение: кандидат всё ещё внутри полигона — пропускаем эту пару!


In [33]:
# ------------------------------
# 6. Визуализация на карте с Folium
# ------------------------------

m = folium.Map(location=[drone_data["lat"], drone_data["lng"]], zoom_start=16)

# Отображаем сохранённый полигон
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)

# Добавляем маркер дрона
folium.Marker(
    [drone_data["lat"], drone_data["lng"]],
    popup='Дрон',
    icon=folium.Icon(color='red', icon='info-sign')
).add_to(m)

# Отображаем исходный маршрут (если есть) – например, синяя пунктирная линия
if route_points:
    folium.PolyLine(
        locations=[(pt["lat"], pt["lng"]) for pt in route_points],
        color="blue",
        weight=3,
        opacity=0.7,
        dash_array="5,5"
    ).add_to(m)


# # Отображаем safe_points (оранжевые кружки)
# for pt in safe_points_wgs:
#     folium.CircleMarker(
#         location=pt, radius=3, color='orange', fill=True, fill_color='orange'
#     ).add_to(m)

# Отображаем boundary_points (например, фиолетовые кружки)
for pt in boundary_points_wgs:
    folium.CircleMarker(location=pt, radius=2, color='purple', fill=True, fill_color='purple').add_to(m)

# Отображаем corrected точки (зелёные кружки)
for pt in corrected_points_wgs:
    folium.CircleMarker(
        location=pt,
        radius=2,
        color='green',
        fill=True,
        fill_color='green'
    ).add_to(m)

# Соединяем corrected точки линией (скорректированная миссия)
if corrected_points_wgs:
    folium.PolyLine(
        locations=corrected_points_wgs,
        color="green",
        weight=3,
        opacity=0.8
    ).add_to(m)

m

In [29]:
# # ------------------------------
# # 2. Преобразование координат: UTM <-> WGS84
# # ------------------------------
#
# # Для Москвы часто используют UTM zone 37N (EPSG:32637)
# # transformer_to_m = Transformer.from_crs("epsg:4326", "epsg:32637", always_xy=True)
# # transformer_to_wgs = Transformer.from_crs("epsg:32637", "epsg:4326", always_xy=True)
#
def utm_point_to_wgs(pt):
    """Преобразует shapely Point из UTM в (lat, lng)"""
    lng, lat = transformer_to_wgs.transform(pt.x, pt.y)
    return (lat, lng)

# Функция для преобразования полигона из WGS84 в UTM.
def transform_polygon_to_utm(poly_wgs, transformer):
    coords = list(poly_wgs.exterior.coords)
    # Убедимся, что контур замкнут
    if coords[0] != coords[-1]:
        coords.append(coords[0])
    utm_coords = [transformer.transform(lon, lat) for (lon, lat) in coords]
    return Polygon(utm_coords)

# Преобразуем первый полигон из saved_polygons в UTM
from shapely.geometry import shape
if len(saved_polygons["features"]) > 0:
    poly_wgs = shape(saved_polygons["features"][0]["geometry"])
    poly_utm = transform_polygon_to_utm(poly_wgs, transformer_to_m)
else:
    raise ValueError("Нет сохранённых полигонов.")

# ------------------------------
# 3. Преобразование boundary_points_wgs в объекты Point в UTM
# ------------------------------
boundary_points_utm = []
for lat, lng in boundary_points_wgs:
    x, y = transformer_to_m.transform(lng, lat)
    boundary_points_utm.append(Point(x, y))

# ------------------------------
# 4. Функция смещения точки наружу
# ------------------------------
def shift_point_outward(point, poly, offset_distance):
    """
    Смещает точку, лежащую на границе полигона (poly), наружу.
    Используется вектор, направленный от центра полигона к точке.

    point: shapely Point в UTM (точка на границе полигона)
    poly: shapely Polygon в UTM
    offset_distance: смещение в метрах
    Возвращает новую точку (shapely Point в UTM)
    """
    centroid = poly.centroid
    # Вектор от центра полигона к точке
    vec = np.array([point.x - centroid.x, point.y - centroid.y])
    norm = np.linalg.norm(vec)
    if norm == 0:
        return point
    unit_vec = vec / norm
    # Смещаем точку наружу на offset_distance вдоль этого вектора
    shifted_coords = np.array([point.x, point.y]) + offset_distance * unit_vec
    shifted_point = Point(shifted_coords)
    # Дополнительная проверка: если точка оказывается внутри полигона, смещаем в обратном направлении
    if poly.contains(shifted_point):
        shifted_coords = np.array([point.x, point.y]) - offset_distance * unit_vec
        shifted_point = Point(shifted_coords)
    return shifted_point

# ------------------------------
# 5. Смещение всех точек из boundary_points_utm наружу
# ------------------------------
offset_distance = 3.0  # смещение в метрах
shifted_points_utm = [shift_point_outward(pt, poly_utm, offset_distance) for pt in boundary_points_utm]

# Преобразуем исходные и смещённые точки обратно в WGS84
boundary_points_wgs_converted = [utm_point_to_wgs(pt) for pt in boundary_points_utm]
shifted_points_wgs = [utm_point_to_wgs(pt) for pt in shifted_points_utm]

# ------------------------------
# 6. Визуалзация на карте с Folium
# ------------------------------
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=16)

# Функция преобразования (lng, lat) -> (lat, lng)
def to_latlon(coord):
    return (coord[1], coord[0])

# Отображаем сохранённые полигоны
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)

# Отображаем исходные boundary точки (синие кружки)
for pt in boundary_points_wgs_converted:
    folium.CircleMarker(location=pt, radius=3, color='blue', fill=True, fill_color='blue').add_to(m)

# Отображаем смещённые точки (красные кружки)
for pt in shifted_points_wgs:
    folium.CircleMarker(location=pt, radius=3, color='red', fill=True, fill_color='red').add_to(m)

# Соединяем каждую исходную точку с её смещённой точкой (фиолетовая пунктирная линия)
for orig, shifted in zip(boundary_points_wgs_converted, shifted_points_wgs):
    folium.PolyLine(locations=[orig, shifted], color='purple', weight=2, opacity=0.8, dash_array='2,4').add_to(m)

# Маркер дрона (черный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон', icon=folium.Icon(color='black', icon='info-sign')
).add_to(m)

m

In [30]:
import numpy as np
import folium
from shapely.geometry import Polygon, Point, LineString, shape
from pyproj import Transformer

# ===============================
# 1. Исходные данные
# ===============================
# drone_data = {'lat': 55.139592, 'lng': 37.962471, 'altitude': 0}

# # Пример массива точек, полученных ранее из скорректированного маршрута, лежащих на границе полигона (в формате (lat, lng))
# boundary_points_wgs = [
#     (55.1409, 37.9630),
#     (55.1410, 37.9627),
#     (55.1408, 37.9629),
#     (55.1407, 37.9628)
# ]
#
# # Пример сохранённого полигона (GeoJSON)
# saved_polygons = {
#     "type": "FeatureCollection",
#     "features": [
#         {
#             "id": "poly1",
#             "type": "Feature",
#             "properties": {},
#             "geometry": {
#                 "type": "Polygon",
#                 "coordinates": [[[37.962317690128344, 55.140717794429236],
#                                  [37.96225339073058, 55.14161451238664],
#                                  [37.96256202783857, 55.14165861274998],
#                                  [37.96290924458515, 55.14115145562934],
#                                  [37.96284494518832, 55.14068839349923],
#                                  [37.962613467357244, 55.14070309396709],
#                                  [37.962317690128344, 55.140717794429236]]]
#             }
#         }
#     ]
# }

# ===============================
# 2. Преобразование координат: WGS84 <-> UTM
# ===============================
# Для Москвы часто используют UTM zone 37N (EPSG:32637)
transformer_to_m = Transformer.from_crs("epsg:4326", "epsg:32637", always_xy=True)
transformer_to_wgs = Transformer.from_crs("epsg:32637", "epsg:4326", always_xy=True)

def utm_point_to_wgs(pt):
    lng, lat = transformer_to_wgs.transform(pt.x, pt.y)
    return (lat, lng)

def transform_polygon_to_utm(poly_wgs, transformer):
    coords = list(poly_wgs.exterior.coords)
    if coords[0] != coords[-1]:
        coords.append(coords[0])
    utm_coords = [transformer.transform(lon, lat) for (lon, lat) in coords]
    return Polygon(utm_coords)

from shapely.geometry import shape
poly_wgs = shape(saved_polygons["features"][0]["geometry"])
poly_utm = transform_polygon_to_utm(poly_wgs, transformer_to_m)

# ===============================
# 3. Преобразование boundary_points_wgs в объекты Point в UTM
# ===============================
boundary_points_utm = []
for lat, lng in boundary_points_wgs:
    x, y = transformer_to_m.transform(lng, lat)
    boundary_points_utm.append(Point(x, y))

# ===============================
# 4. Функция смещения точек наружу (на основе центра полигона)
# ===============================
def shift_point_outward(point, poly, offset_distance):
    """
    Смещает точку, лежащую на границе полигона, наружу от полигона.
    Вычисляется вектор от центра полигона к точке.

    point: shapely Point в UTM (точка на границе полигона)
    poly: shapely Polygon в UTM
    offset_distance: смещение в метрах
    """
    centroid = poly.centroid
    vec = np.array([point.x - centroid.x, point.y - centroid.y])
    norm = np.linalg.norm(vec)
    if norm == 0:
        return point
    unit_vec = vec / norm
    shifted_coords = np.array([point.x, point.y]) + offset_distance * unit_vec
    shifted_point = Point(shifted_coords)
    if poly.contains(shifted_point):
        shifted_coords = np.array([point.x, point.y]) - offset_distance * unit_vec
        shifted_point = Point(shifted_coords)
    return shifted_point

# ===============================
# 5. Функция для уточнения (разбивки) острых углов
# ===============================
def refine_boundary(shifted_boundary):
    """
    Принимает массив точек (shifted_boundary) в UTM, возвращает новый массив с дополнительными
    точками в местах острых углов.
    Если угол между двумя сегментами меньше порогового (например, 45 градусов), добавляет дополнительную точку.
    """
    refined = []
    n = len(shifted_boundary)
    for i in range(n):
        p_prev = np.array(shifted_boundary[i - 1])
        p_curr = np.array(shifted_boundary[i])
        p_next = np.array(shifted_boundary[(i + 1) % n])
        v1 = p_curr - p_prev
        v2 = p_next - p_curr
        norm1 = np.linalg.norm(v1)
        norm2 = np.linalg.norm(v2)
        if norm1 == 0 or norm2 == 0:
            angle_deg = 180.0
        else:
            v1_norm = v1 / norm1
            v2_norm = v2 / norm2
            dot = np.dot(v1_norm, v2_norm)
            dot = np.clip(dot, -1.0, 1.0)
            angle = np.arccos(dot)
            angle_deg = np.degrees(angle)
        refined.append(tuple(p_curr))
        if angle_deg < 45:
            # Добавляем промежуточную точку между p_curr и p_next
            mid = tuple((p_curr + p_next) / 2)
            refined.append(mid)
    return refined

# ===============================
# 6. Смещение точек и уточнение
# ===============================
offset_distance = 3.0  # смещение наружу в метрах

# Для каждой точки из boundary_points_utm вычисляем смещённую точку наружу
shifted_points_utm = [shift_point_outward(pt, poly_utm, offset_distance) for pt in boundary_points_utm]

# Опционально уточняем набор смещённых точек для острых углов
refined_points_utm = refine_boundary([ (pt.x, pt.y) for pt in shifted_points_utm ])

# Преобразуем refined_points_utm в объекты Point
refined_points_utm = [Point(pt) for pt in refined_points_utm]

# Преобразуем исходные boundary точки и смещённые точки обратно в WGS84
boundary_points_wgs_converted = [utm_point_to_wgs(pt) for pt in boundary_points_utm]
shifted_points_wgs = [utm_point_to_wgs(pt) for pt in refined_points_utm]

# ===============================
# 7. Визуализация на карте с Folium
# ===============================
m = folium.Map(location=[drone_data['lat'], drone_data['lng']], zoom_start=17)

# Отображаем сохранённый полигон
folium.GeoJson(
    saved_polygons,
    style_function=lambda x: {'fillColor': 'gray', 'color': 'black', 'weight': 2, 'fillOpacity': 0.3}
).add_to(m)

# Отображаем исходные boundary точки (синие кружки)
for pt in boundary_points_wgs_converted:
    folium.CircleMarker(location=pt, radius=3, color='blue', fill=True, fill_color='blue').add_to(m)

# Отображаем смещённые (refined) точки (красные кружки)
for pt in shifted_points_wgs:
    folium.CircleMarker(location=pt, radius=3, color='red', fill=True, fill_color='red').add_to(m)

# Соединяем каждую исходную точку с её смещённой точкой линией (фиолетовая пунктирная)
# for orig, shifted in zip(boundary_points_wgs_converted, shifted_points_wgs):
#     folium.PolyLine(locations=[orig, shifted], color='purple', weight=2, opacity=0.8, dash_array='2,4').add_to(m)

# Маркер дрона (черный)
folium.Marker(
    [drone_data['lat'], drone_data['lng']],
    popup='Дрон', icon=folium.Icon(color='black', icon='info-sign')
).add_to(m)

m